# Reinforcement Learning control strategies for Electric Vehicles fleet Virtual Power Plants
Thesis based on the development of a RL agent that manages a VPP through EVs charging stations in an household environment. Main optimization objectives of the VPP are: Valley filling, peak shaving and zero resulting load over time. Main action performed to reach objectives are: storage of Renewable energy resources and power push in the grid at high demand times. The development of the Virtual Power Plant environment is based on the ELVIS (Electric Vehicles Infrastructure Simulator) open library from DAI-Labor: https://github.com/dailab/elvis The thesis code is currently available at: (https://github.com/francescomaldonato/RL_VPP_Thesis)

Author: Francesco Maldonato

## VPP simulator Notebook based on EVs arrival, with StableBaselines3 trained model (Recurrent PPO)

Installing required packages and dependencies

In [1]:
%%capture
!pip install py-elvis==0.2.1
!pip install pyyaml==5.4
!pip install plotly==5.9.0
!pip install -U kaleido==0.2.1

!pip install stable-baselines3[extra]==1.6.1
!pip install stable-baselines==1.6.1
!pip install sb3-contrib==1.6.1
!pip install gym==0.20.0
!pip install -q wandb==0.13.4

In [3]:
#Cloning repository and changing directory
!git clone https://github.com/francescomaldonato/RL_VPP_Thesis.git
%cd RL_VPP_Thesis/
%ls

In [4]:
import yaml
import numpy as np
from gym import Env
from VPP_environment import VPPEnv, VPP_Scenario_config
from elvis.config import ScenarioConfig
import os
import torch
import random
import wandb
from sb3_contrib import RecurrentPPO #The available algoritmhs in sb3-contrib for the custom environment with MultiInputPolicy
from sb3_contrib.common.maskable.utils import get_action_masks
import stable_baselines3 as sb3
from stable_baselines3.common.env_checker import check_env

#Check if cuda device is available for training
print("Torch-Cuda available device:", torch.cuda.is_available())
print(sb3.get_system_info())
#!wandb --version

Torch-Cuda available device: False
OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022
Python: 3.7.14
Stable-Baselines3: 1.6.1
PyTorch: 1.12.1+cu113
GPU Enabled: False
Numpy: 1.21.6
Gym: 0.20.0

({'OS': 'Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022', 'Python': '3.7.14', 'Stable-Baselines3': '1.6.1', 'PyTorch': '1.12.1+cu113', 'GPU Enabled': 'False', 'Numpy': '1.21.6', 'Gym': '0.20.0'}, 'OS: Linux-5.10.133+-x86_64-with-Ubuntu-18.04-bionic #1 SMP Fri Aug 26 08:44:51 UTC 2022\nPython: 3.7.14\nStable-Baselines3: 1.6.1\nPyTorch: 1.12.1+cu113\nGPU Enabled: False\nNumpy: 1.21.6\nGym: 0.20.0\n')


In [5]:
# Ensure deterministic behavior
torch.backends.cudnn.deterministic = True
random.seed(0)
torch.manual_seed(0)
torch.cuda.manual_seed_all(0)

## Load ELVIS YAML config file
Section where the EVs arrival simulation parameters are loaded through the Yaml config file from the 'data/config_builder/' folder.

In [6]:
#Loading paths for input data
current_folder = ''
VPP_training_data_input_path = current_folder + 'data/data_training/environment_table/' + 'Environment_data_2019.csv'
VPP_testing_data_input_path = current_folder + 'data/data_testing/environment_table/' + 'Environment_data_2020.csv'
VPP_validating_data_input_path = current_folder + 'data/data_validating/environment_table/' + 'Environment_data_2018.csv'
elvis_input_folder = current_folder + 'data/config_builder/'

case = 'wohnblock_household_simulation_adaptive.yaml' #(loaded by default, 20 EVs arrivals per week with 50% average battery)

#Try different simulation parameters, uncomment below
#case = 'wohnblock_household_simulation_adaptive_30.yaml' #(30 EVs arrivals per week with 65% average battery) 
#case = 'wohnblock_household_simulation_adaptive_18.yaml' #(18 EVs arrivals per week with 40% average battery) 
#case = 'wohnblock_household_simulation_adaptive_22.yaml' #(22 EVs arrivals per week with 55% average battery) 

with open(elvis_input_folder + case, 'r') as file:
    yaml_str = yaml.full_load(file)

elvis_config_file = ScenarioConfig.from_yaml(yaml_str)
VPP_config_file = VPP_Scenario_config(yaml_str)

print(elvis_config_file)
print(VPP_config_file)

Vehicle types: <generator object ScenarioConfig.__str__.<locals>.<genexpr> at 0x7f0108ca6cd0>Mean parking time: 23.99
Std deviation of parking time: 1
Mean value of the SOC distribution: 0.5
Std deviation of the SOC distribution: 0.1
Max parking time: 24
Number of charging events per week: 20
Vehicles are disconnected only depending on their parking time
Queue length: 0
Opening hours: None
Scheduling policy: Uncontrolled

{'start_date': '2022-01-01T00:00:00', 'end_date': '2023-01-01T00:00:00', 'resolution': '0:15:00', 'num_households': 4, 'solar_power': 16, 'wind_power': 12, 'EV_types': [{'battery': {'capacity': 100, 'efficiency': 1, 'max_charge_power': 150, 'min_charge_power': 0}, 'brand': 'Tesla', 'model': 'Model S', 'probability': 1}], 'charging_stations_n': 4, 'EVs_n': 20, 'EVs_n_max': 1044, 'mean_park': 23.99, 'std_deviation_park': 1, 'EVs_mean_soc': 50.0, 'EVs_std_deviation_soc': 10.0, 'EV_load_max': 44, 'EV_load_rated': 14.8, 'EV_load_min': 1, 'houseRWload_max': 10, 'av_max_ener

In [7]:
#TESTING Environment initialization
env = VPPEnv(VPP_testing_data_input_path, elvis_config_file, VPP_config_file)
env.plot_VPP_input_data()

Output hidden; open in https://colab.research.google.com to view.

In [8]:
env.plot_ELVIS_data()

In [9]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
env.plot_reward_functions()

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  21111.16 , over-consume=kWh  38806.38 , under-consume=kWh  17695.22 , Total_cost=€  870.39 , overcost=€  1373.85 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....


### VPP Simulation test with random actions [no model loaded]

In [10]:
episodes = 1
for episode in range(1, episodes+1):
    state = env.reset()
    done = False
    score = 0
    while not done:
        action_masks = get_action_masks(env)
        action = env.action_space.sample()
        
        n_state, reward, done, info = env.step(action)
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [11]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [12]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [13]:
env.plot_VPP_Elvis_comparison()

In [14]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [15]:
env.plot_rewards_stats()

In [16]:
env.plot_EVs_kpi()

In [17]:
env.plot_actions_kpi()

In [18]:
env.plot_load_kpi()

In [19]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [20]:
## Wandb login to load models
#In Colab, uncomment below:
# %env "WANDB_DISABLE_CODE" True
# %env "WANDB_NOTEBOOK_NAME" "VPP_simulator.ipynb"
# os.environ['WANDB_NOTEBOOK_NAME'] = 'VPP_simulator.ipynb'
#wandb.login(relogin=True)

#In local notebook, uncomment below:
#your_wandb_login_code = 0123456789abcdefghijklmnopqrstwxyzàèìòù0 #example length
#!wandb login {your_wandb_login_code}

In [21]:
#Loading training model, from local directory or from wandb previous trainings
RecurrentPPO_path = "trained_models/RecurrentPPO_models/model_RecurrentPPO_"

#model_id = "s37o8q0n"
model_id = "333ckz0i"
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

# run_id_restore = "2y2dqvyn"
# model = wandb.restore(f'model_{run_id_restore}.zip', run_path=f"francesco_maldonato/RL_VPP_Thesis/{run_id_restore}")

/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


## Testing dataset VPP Simulation using the loaded trained model

In [22]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

#Save the VPP table
VPP_table = env.save_VPP_table(save_path='data/environment_optimized_output/VPP_table.csv')

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  22490.82 , over-consume=kWh  39799.65 , under-consume=kWh  17308.83 , Total_cost=€  915.17 , overcost=€  1410.14 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  75.08
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -3918.58 , over-consume=KWh  1901.41 , under-consume=KWh  5820.0 , Total_cost=€  -82.47 , Overcost=€  65.19 
 EV_INFO: Av.EV_energy_leaving=kWh  66.06 , Std.EV_energy_leaving=kWh  24.22 , EV_departures =  1046 , EV_queue_left =  0
SCORE:  Cumulative_reward= 412720.7 - Step_rewars (load_t= 376537.92, EVs_energy_t= 13037.94)
 - Final_rewards (EVs_energy= 15617.15, Overconsume= -1133.66, Underconsume= -2554.58, Overcost= 11215.95)
Episode:1 Score:412720.70314517245


In [23]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [24]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00  67.120514  67.111046  51.303707  35.395222   
2022-01-01 00:15:00  67.370514  66.489479  50.682140  35.645222   
2022-01-01 00:30:00  67.620514  65.939354  50.132011  35.895222   
2022-01-01 00:45:00  67.870514  65.545929  49.738586  36.145222   
2022-01-01 01:00:00  68.120514  65.214035  49.406693  36.395222   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  67.663498   0.000000  99.989998   0.000000   
2022-06-06 05:00:00  67.663498   0.000000  99.989998   0.000000   
2022-06-06 05:15:00  67.663498   0.000000  99.989998   0.000000   
2022-06-06 05:30:00  67.663498   0.000000  99.989998   0.000000   
2022-06-06 05:45:00  67.663498   0.000000  99.989998   0.000000   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [1, 2, 2, 1]   
2022-01-01 00:15:00  [3126, 3127, 3128, 3129]  [1, 2, 2, 1]   
2022-01-01 00:30:00  [3126, 3127, 3128, 3129]  [1, 2, 2, 1]   
2022-01-01 00:45:00  [3126, 3127, 3128, 3129]  [1, 2, 2, 1]   
2022-01-01 01:00:00  [3126, 3127, 3128, 3129]  [1, 2, 2, 1]   
...                                       ...           ...   
2022-06-06 04:45:00        [3577, 0, 3576, 0]  [0, 0, 1, 2]   
2022-06-06 05:00:00        [3577, 0, 3576, 0]  [0, 0, 1, 2]   
2022-06-06 05:15:00        [3577, 0, 3576, 0]  [0, 0, 1, 2]   
2022-06-06 05:30:00        [3577, 0, 3576, 0]  [0, 0, 1, 2]   
2022-06-06 05:45:00        [3577, 0, 3576, 0]  [0, 0, 1, 2]   

                                       mask_truth          load  load_reward  \
time                                                                           
2022-01-01 00:00:00  [False, False, False, False]  1.204208e+00    15.000000   
2022-01-01 00:15:00    [False, True, True, False] -4.440892e-16    15.000000   
2022-01-01 00:30:00    [False, True, True, False]  4.440892e-16    15.000000   
2022-01-01 00:45:00    [False, True, True, False]  0.000000e+00    15.000000   
2022-01-01 01:00:00    [False, True, True, False]  1.110223e-16    15.000000   
...                                           ...           ...          ...   
2022-06-06 04:45:00   [False, True, False, False] -7.443423e+00   -12.196101   
2022-06-06 05:00:00   [False, True, False, False] -1.191571e+01   -13.125689   
2022-06-06 05:15:00   [False, True, False, False] -1.293826e+01   -12.386428   
2022-06-06 05:30:00   [False, True, False, False] -1.212507e+01   -12.110279   
2022-06-06 05:45:00   [False, True, False, False] -1.182131e+01   -12.939513   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  15.000000  
2022-01-01 00:15:00        0.0  15.000000  
2022-01-01 00:30:00        0.0  15.000000  
2022-01-01 00:45:00        0.0  15.000000  
2022-01-01 01:00:00        0.0  15.000000  
...                        ...        ...  
2022-06-06 04:45:00        0.0 -12.196101  
2022-06-06 05:00:00        0.0 -13.125689  
2022-06-06 05:15:00        0.0 -12.386428  
2022-06-06 05:30:00        0.0 -12.110279  
2022-06-06 05:45:00        0.0 -12.939513  

[15000 rows x 11 columns]

In [25]:
env.plot_Elvis_results()

Output hidden; open in https://colab.research.google.com to view.

In [26]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [27]:
env.plot_VPP_Elvis_comparison()

In [28]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [29]:
env.plot_rewards_stats()

In [30]:
env.plot_EVs_kpi()

In [31]:
env.plot_load_kpi()

In [32]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Validating dataset VPP Simulation using the loaded trained model

In [33]:
#VALIDATING Environment initialization
env = VPPEnv(VPP_validating_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 4173, Arrival time: 2022-01-01 08:45:00, Parking_time: 23.65620992172503, Leaving_time: 2022-01-02 08:24:22.355718, SOC: 0.5912146677222658, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 5215, Arrival time: 2022-12-31 16:45:00, Parking_time: 23.669372318041177, Leaving_time: 2023-01-01 16:25:09.740345, SOC: 0.641443061071843, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -30085.39 , over-consume=kWh  2136.67 , under-consume=kWh  -32222.06 , Total_cost=€  -1187.15 , overcost=€  113.34
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  12603.16 , over-consume=kWh  33639.57 , under-consume=kWh  21036.41 , Total_cost=€  616.46 , overcost=€  1469.82 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89


In [34]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [35]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [36]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  11890.17 , over-consume=kWh  33446.92 , under-consume=kWh  21556.75 , Total_cost=€  582.69 , overcost=€  1456.61 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  80.89
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -7323.81 , over-consume=KWh  1379.36 , under-consume=KWh  8703.17 , Total_cost=€  -260.29 , Overcost=€  60.17 
 EV_INFO: Av.EV_energy_leaving=kWh  72.35 , Std.EV_energy_leaving=kWh  22.72 , EV_departures =  1039 , EV_queue_left =  0
SCORE:  Cumulative_reward= 400672.31 - Step_rewars (load_t= 340200.6, EVs_energy_t= 34073.55)
 - Final_rewards (EVs_energy= 18933.18, Overconsume= -866.95, Underconsume= -3819.99, Overcost= 12151.92)
Episode:1 Score:400672.30800519156


In [37]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [38]:
VPP_table.head(15000)

0          1          2          3  \
time                                                              
2022-01-01 00:00:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:15:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:30:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 00:45:00   0.000000   0.000000   0.000000   0.000000   
2022-01-01 01:00:00   0.000000   0.000000   0.000000   0.000000   
...                        ...        ...        ...        ...   
2022-06-06 04:45:00  87.425644  46.645950  36.731659  82.234077   
2022-06-06 05:00:00  88.267708  47.488014  37.573723  83.076141   
2022-06-06 05:15:00  89.193504  48.413815  38.499523  84.001938   
2022-06-06 05:30:00  90.031441  49.251747  39.337456  84.839874   
2022-06-06 05:45:00  90.890244  50.110546  40.196255  85.698677   

                                       EVs_id       actions  \
time                                                          
2022-01-01 00:00:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00              [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00              [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                       ...           ...   
2022-06-06 04:45:00  [6691, 6689, 6692, 6690]  [1, 1, 1, 1]   
2022-06-06 05:00:00  [6691, 6689, 6692, 6690]  [1, 1, 1, 1]   
2022-06-06 05:15:00  [6691, 6689, 6692, 6690]  [1, 1, 1, 1]   
2022-06-06 05:30:00  [6691, 6689, 6692, 6690]  [1, 1, 1, 1]   
2022-06-06 05:45:00  [6691, 6689, 6692, 6690]  [1, 1, 1, 1]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -4.084642    -4.930044   
2022-01-01 00:15:00  [False, False, False, True] -3.958026    -4.109670   
2022-01-01 00:30:00  [False, False, False, True] -3.465802    -4.190114   
2022-01-01 00:45:00  [False, False, False, True] -3.514068    -5.119939   
2022-01-01 01:00:00   [False, True, False, True] -4.131933    -5.483384   
...                                          ...       ...          ...   
2022-06-06 04:45:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:00:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:15:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:30:00     [True, True, True, True]  0.000000    15.000000   
2022-06-06 05:45:00     [True, True, True, True]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -4.930044  
2022-01-01 00:15:00        0.0  -4.109670  
2022-01-01 00:30:00        0.0  -4.190114  
2022-01-01 00:45:00        0.0  -5.119939  
2022-01-01 01:00:00        0.0  -5.483384  
...                        ...        ...  
2022-06-06 04:45:00        0.0  15.000000  
2022-06-06 05:00:00        0.0  15.000000  
2022-06-06 05:15:00        0.0  15.000000  
2022-06-06 05:30:00        0.0  15.000000  
2022-06-06 05:45:00        0.0  15.000000  

[15000 rows x 11 columns]

In [39]:
env.plot_VPP_results()


Output hidden; open in https://colab.research.google.com to view.

In [40]:
env.plot_VPP_Elvis_comparison()

In [41]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [42]:
env.plot_rewards_stats()

In [43]:
env.plot_EVs_kpi()

In [44]:
env.plot_load_kpi()

In [45]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

## Training dataset VPP Simulation using the loaded trained model

In [46]:
#TRAINING Environment initialization
env = VPPEnv(VPP_training_data_input_path, elvis_config_file, VPP_config_file)

Charging event: 7302, Arrival time: 2022-01-03 16:30:00, Parking_time: 24, Leaving_time: 2022-01-04 16:30:00, SOC: 0.40195440395377446, SOC target: 1.0, Connected car: Tesla, Model S 
 ... 
 Charging event: 8344, Arrival time: 2022-12-31 23:45:00, Parking_time: 24, Leaving_time: 2023-01-01 23:45:00, SOC: 0.39914027190377505, SOC target: 1.0, Connected car: Tesla, Model S 

-DATASET: House&RW_energy_sum=kWh  -34117.7 , over-consume=kWh  1556.25 , under-consume=kWh  -35673.95 , Total_cost=€  -1196.64 , overcost=€  97.86
- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8857.49 , over-consume=kWh  32344.25 , under-consume=kWh  23486.76 , Total_cost=€  490.16 , overcost=€  1352.42 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2


In [47]:
#Function to check custom environment and output additional warnings if needed
check_env(env)
plot_VPP_input_data = env.plot_VPP_input_data()
plot_VPP_input_data.show()

Output hidden; open in https://colab.research.google.com to view.

In [48]:
#model = PPO.load(PPO_path + model_run_ID, env = env)
model = RecurrentPPO.load(RecurrentPPO_path + model_id, env=env)

Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


/usr/local/lib/python3.7/dist-packages/stable_baselines3/common/save_util.py:169: UserWarning:

Could not deserialize object _last_lstm_states. Consider using `custom_objects` argument to replace this object.



In [49]:
#TEST Model
episodes = 1
for episode in range(1, episodes+1):
    obs = env.reset()
    done = False
    score = 0
    # cell and hidden state of the LSTM
    lstm_states = None
    num_envs = 1
    # Episode start signals are used to reset the lstm states
    episode_starts = np.ones((num_envs,), dtype=bool)
    while not done:
        #env.render()
        action_masks = get_action_masks(env)
        action, lstm_states = model.predict(obs, state=lstm_states, episode_start=episode_starts, deterministic=True) #Now using our trained model with deterministic prediction [should improve performances]
        env.lstm_state = lstm_states
        obs, reward, done, info = env.step(action)
        episode_starts = done
        score+=reward
    print('Episode:{} Score:{}'.format(episode, score))

VPP_table = env.VPP_table
#print(env.lstm_states_list)

- ELVIS.Simulation (Av.EV_SOC=  50.0 %):
 Sum_Energy=kWh  8378.64 , over-consume=kWh  32057.24 , under-consume=kWh  23678.61 , Total_cost=€  473.61 , overcost=€  1339.92 , Av.EV_en_left=kWh  100.0 , Charging_events=  1043 
- Exp.VPP_goals: Energy_consumed=kWh 0, Av.load=kW 0, Std.load=kW 0, Total_cost=€ 0 , Av.EV_en_left=kWh  84.2
Simulating VPP....
- VPP.Simulation results
 LOAD_INFO: Sum_Energy=KWh  -8836.54 , over-consume=KWh  1317.1 , under-consume=KWh  10153.64 , Total_cost=€  -307.0 , Overcost=€  53.15 
 EV_INFO: Av.EV_energy_leaving=kWh  74.68 , Std.EV_energy_leaving=kWh  22.26 , EV_departures =  1043 , EV_queue_left =  0
SCORE:  Cumulative_reward= 396601.8 - Step_rewars (load_t= 329648.12, EVs_energy_t= 40783.72)
 - Final_rewards (EVs_energy= 18856.95, Overconsume= -860.65, Underconsume= -4290.2, Overcost= 12463.86)
Episode:1 Score:396601.7964414954


In [50]:
env.plot_VPP_energies()

Output hidden; open in https://colab.research.google.com to view.

In [51]:
VPP_table.head(14995)

0          1          2    3  \
time                                                        
2022-01-01 00:00:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:15:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:30:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 00:45:00   0.000000   0.000000   0.000000  0.0   
2022-01-01 01:00:00   0.000000   0.000000   0.000000  0.0   
...                        ...        ...        ...  ...   
2022-06-06 03:30:00  60.202995  82.934525  65.263855  0.0   
2022-06-06 03:45:00  60.564255  83.295784  65.625114  0.0   
2022-06-06 04:00:00  61.084301  83.815826  66.145157  0.0   
2022-06-06 04:15:00  61.894993  83.815826  66.955849  0.0   
2022-06-06 04:30:00  62.698582  83.815826  67.759438  0.0   

                                    EVs_id       actions  \
time                                                       
2022-01-01 00:00:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:15:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:30:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 00:45:00           [0, 0, 0, 0]  [2, 1, 1, 0]   
2022-01-01 01:00:00           [0, 0, 0, 0]  [2, 0, 1, 0]   
...                                    ...           ...   
2022-06-06 03:30:00  [9878, 9879, 9877, 0]  [1, 1, 1, 2]   
2022-06-06 03:45:00  [9878, 9879, 9877, 0]  [1, 1, 1, 2]   
2022-06-06 04:00:00  [9878, 9879, 9877, 0]  [1, 0, 1, 2]   
2022-06-06 04:15:00  [9878, 9879, 9877, 0]  [1, 0, 1, 2]   
2022-06-06 04:30:00  [9878, 9879, 9877, 0]  [1, 0, 1, 2]   

                                      mask_truth      load  load_reward  \
time                                                                      
2022-01-01 00:00:00  [False, False, False, True] -3.624760    -2.565697   
2022-01-01 00:15:00  [False, False, False, True] -2.539418    -4.494385   
2022-01-01 00:30:00  [False, False, False, True] -3.696631    -4.388487   
2022-01-01 00:45:00  [False, False, False, True] -3.633092    -4.843988   
2022-01-01 01:00:00   [False, True, False, True] -3.906393    -6.526745   
...                                          ...       ...          ...   
2022-06-06 03:30:00    [True, True, True, False]  0.000000    15.000000   
2022-06-06 03:45:00    [True, True, True, False]  0.000000    15.000000   
2022-06-06 04:00:00    [True, True, True, False]  0.000000    15.000000   
2022-06-06 04:15:00    [True, True, True, False]  0.000000    15.000000   
2022-06-06 04:30:00    [True, True, True, False]  0.000000    15.000000   

                     EV_reward    rewards  
time                                       
2022-01-01 00:00:00        0.0  -2.565697  
2022-01-01 00:15:00        0.0  -4.494385  
2022-01-01 00:30:00        0.0  -4.388487  
2022-01-01 00:45:00        0.0  -4.843988  
2022-01-01 01:00:00        0.0  -6.526745  
...                        ...        ...  
2022-06-06 03:30:00        0.0  15.000000  
2022-06-06 03:45:00        0.0  15.000000  
2022-06-06 04:00:00        0.0  15.000000  
2022-06-06 04:15:00        0.0  15.000000  
2022-06-06 04:30:00        0.0  15.000000  

[14995 rows x 11 columns]

In [52]:
env.plot_VPP_results()

Output hidden; open in https://colab.research.google.com to view.

In [53]:
env.plot_VPP_Elvis_comparison()

In [54]:
env.plot_rewards_results()

Output hidden; open in https://colab.research.google.com to view.

In [55]:
env.plot_rewards_stats()

In [56]:
env.plot_EVs_kpi()

In [57]:
env.plot_actions_kpi()

In [58]:
env.plot_load_kpi()

In [59]:
env.plot_yearly_load_log()

Output hidden; open in https://colab.research.google.com to view.

In [60]:
#env.close()